# Create coco dataset:

Use this notebook to transform the data from the segmentation into a Coco dataset that can be used by Mask-RCNN. Most importantly, the annotation file needs to be created, which links the images to their corresponding masks.

The file tree for this procedure to work must be of the form: 
    
    cells_to_coco.ipynb
    |
    |
    --- \data 
        |
        |
        --- \cells_setname2020 (contains the images of the corresponding set (train, validate, test) in .png format
        |
        |
        --- \annotations (contains the individual binary masks of the images in .png format, annotation files will be stored here)
        

That means, especially, that after performing the segmentation step the 'vanilla' images need to be moved to the corresponding setname folder randomly. 

For naming, it is important that the annotation files contain the name of the corresponding cell type.

In [3]:
import datetime
import json
import os
import re
import fnmatch
from PIL import Image
import numpy as np
from pycococreatortools import pycococreatortools

In [12]:
#Global variables
#Denote the current set (train, validate, test)
setname = 'train'
ROOT_DIR = 'data-cells2'
IMAGE_DIR = os.path.join(ROOT_DIR, "cells_"+str(setname)+"2020")
ANNOTATION_DIR = os.path.join(ROOT_DIR, "annotations")

In [13]:
#Input certain features of the whole dataset, most importantly the name of the two classes (HEK, MEF)

INFO = {
    "description": "Dataset to" +str(setname) ,
    "url": " ",
    "version": "0.0.1",
    "year": 2020,
    "contributor": "Len",
    "date_created": datetime.datetime.utcnow().isoformat(' ')
}

LICENSES = [
    {
        "id": 1,
        "name": "Attribution-NonCommercial-ShareAlike License",
        "url": "http://creativecommons.org/licenses/by-nc-sa/2.0/"
    }
]

CATEGORIES = [
    {
        'id': 1,
        'name': 'N2a',
        'supercategory': 'cell_type',
    },
    {
        'id': 2,
        'name': 'HEK',
        'supercategory': 'cell_type',
    }
]

In [14]:
#Define functions

#Function to select the .png images from a given path 
def filter_for_png(root, files):
    file_types = ['*.png']
    file_types = r'|'.join([fnmatch.translate(x) for x in file_types])
    files = [os.path.join(root, f) for f in files]
    files = [f for f in files if re.match(file_types, f)]
    
    return files

#Function to select the .png annotations from a given path for a given image 
def filter_for_annotations(root, files, image_filename):
    file_types = ['*.png']
    file_types = r'|'.join([fnmatch.translate(x) for x in file_types])
    non_file_types = ['*mergeMasks.png']
    non_file_types = r'|'.join([fnmatch.translate(x) for x in non_file_types])
    basename_no_extension = os.path.splitext(os.path.basename(image_filename))[0]
    file_name_prefix = basename_no_extension + '.*'
    files = [os.path.join(root, f) for f in files]
    files = [f for f in files if re.match(file_types, f) and not re.match(non_file_types, f)]
    files = [f for f in files if re.match(file_name_prefix, os.path.splitext(os.path.basename(f))[0])]

    return files

In [15]:
#Create the annotation file for the corresponding dataset
def main():

    coco_output = {
        "info": INFO,
        "licenses": LICENSES,
        "categories": CATEGORIES,
        "images": [],
        "annotations": []
    }

    image_id = 1
    segmentation_id = 1
    
    # filter for png images
    for root, _, files in os.walk(IMAGE_DIR):
        image_files = filter_for_png(root, files)

        # go through each image
        for image_filename in image_files:
            image = Image.open(image_filename)
            image_info = pycococreatortools.create_image_info(
                image_id, os.path.basename(image_filename), image.size)
            coco_output["images"].append(image_info)

            # filter for associated png annotations
            for root, _, files in os.walk(ANNOTATION_DIR):
                annotation_files = filter_for_annotations(root, files, image_filename)
                
                # go through each associated annotation
                for annotation_filename in annotation_files:
                    
                    print(annotation_filename)
                    class_id = [x['id'] for x in CATEGORIES if x['name'] in annotation_filename][0]

                    category_info = {'id': class_id, 'is_crowd': 'crowd' in image_filename}
                    binary_mask = np.asarray(Image.open(annotation_filename)
                        .convert('1')).astype(np.uint8)
                    
                    annotation_info = pycococreatortools.create_annotation_info(
                        segmentation_id, image_id, category_info, binary_mask,
                        image.size, tolerance=2)

                    if annotation_info is not None:
                        coco_output["annotations"].append(annotation_info)

                    segmentation_id = segmentation_id + 1

            image_id = image_id + 1

    path = '{}/annotations/instances_cells_'+str(setname)+'2020.json'
    with open(str(path).format(ROOT_DIR), 'w') as output_json_file:
        json.dump(coco_output, output_json_file)

if __name__ == "__main__":
    main()

data-cells2\annotations\HEK_0001_merged_mask_out_1.png
data-cells2\annotations\HEK_0001_merged_mask_out_10.png
data-cells2\annotations\HEK_0001_merged_mask_out_11.png
data-cells2\annotations\HEK_0001_merged_mask_out_12.png
data-cells2\annotations\HEK_0001_merged_mask_out_13.png
data-cells2\annotations\HEK_0001_merged_mask_out_14.png
data-cells2\annotations\HEK_0001_merged_mask_out_15.png
data-cells2\annotations\HEK_0001_merged_mask_out_16.png
data-cells2\annotations\HEK_0001_merged_mask_out_17.png
data-cells2\annotations\HEK_0001_merged_mask_out_18.png
data-cells2\annotations\HEK_0001_merged_mask_out_19.png
data-cells2\annotations\HEK_0001_merged_mask_out_2.png
data-cells2\annotations\HEK_0001_merged_mask_out_20.png
data-cells2\annotations\HEK_0001_merged_mask_out_21.png
data-cells2\annotations\HEK_0001_merged_mask_out_22.png
data-cells2\annotations\HEK_0001_merged_mask_out_23.png
data-cells2\annotations\HEK_0001_merged_mask_out_24.png
data-cells2\annotations\HEK_0001_merged_mask_out_2

data-cells2\annotations\HEK_0003_merged_mask_out_60.png
data-cells2\annotations\HEK_0003_merged_mask_out_61.png
data-cells2\annotations\HEK_0003_merged_mask_out_62.png
data-cells2\annotations\HEK_0003_merged_mask_out_63.png
data-cells2\annotations\HEK_0003_merged_mask_out_64.png
data-cells2\annotations\HEK_0003_merged_mask_out_65.png
data-cells2\annotations\HEK_0003_merged_mask_out_7.png
data-cells2\annotations\HEK_0003_merged_mask_out_8.png
data-cells2\annotations\HEK_0003_merged_mask_out_9.png
data-cells2\annotations\HEK_0004_merged_mask_out_1.png
data-cells2\annotations\HEK_0004_merged_mask_out_10.png
data-cells2\annotations\HEK_0004_merged_mask_out_11.png
data-cells2\annotations\HEK_0004_merged_mask_out_12.png
data-cells2\annotations\HEK_0004_merged_mask_out_13.png
data-cells2\annotations\HEK_0004_merged_mask_out_14.png
data-cells2\annotations\HEK_0004_merged_mask_out_15.png
data-cells2\annotations\HEK_0004_merged_mask_out_16.png
data-cells2\annotations\HEK_0004_merged_mask_out_17.

data-cells2\annotations\HEK_0007_merged_mask_out_41.png
data-cells2\annotations\HEK_0007_merged_mask_out_42.png
data-cells2\annotations\HEK_0007_merged_mask_out_43.png
data-cells2\annotations\HEK_0007_merged_mask_out_44.png
data-cells2\annotations\HEK_0007_merged_mask_out_45.png
data-cells2\annotations\HEK_0007_merged_mask_out_46.png
data-cells2\annotations\HEK_0007_merged_mask_out_47.png
data-cells2\annotations\HEK_0007_merged_mask_out_48.png
data-cells2\annotations\HEK_0007_merged_mask_out_49.png
data-cells2\annotations\HEK_0007_merged_mask_out_5.png
data-cells2\annotations\HEK_0007_merged_mask_out_50.png
data-cells2\annotations\HEK_0007_merged_mask_out_51.png
data-cells2\annotations\HEK_0007_merged_mask_out_52.png
data-cells2\annotations\HEK_0007_merged_mask_out_53.png
data-cells2\annotations\HEK_0007_merged_mask_out_54.png
data-cells2\annotations\HEK_0007_merged_mask_out_55.png
data-cells2\annotations\HEK_0007_merged_mask_out_56.png
data-cells2\annotations\HEK_0007_merged_mask_out_

data-cells2\annotations\HEK_0009_merged_mask_out_1.png
data-cells2\annotations\HEK_0009_merged_mask_out_10.png
data-cells2\annotations\HEK_0009_merged_mask_out_11.png
data-cells2\annotations\HEK_0009_merged_mask_out_12.png
data-cells2\annotations\HEK_0009_merged_mask_out_13.png
data-cells2\annotations\HEK_0009_merged_mask_out_14.png
data-cells2\annotations\HEK_0009_merged_mask_out_15.png
data-cells2\annotations\HEK_0009_merged_mask_out_16.png
data-cells2\annotations\HEK_0009_merged_mask_out_17.png
data-cells2\annotations\HEK_0009_merged_mask_out_18.png
data-cells2\annotations\HEK_0009_merged_mask_out_19.png
data-cells2\annotations\HEK_0009_merged_mask_out_2.png
data-cells2\annotations\HEK_0009_merged_mask_out_20.png
data-cells2\annotations\HEK_0009_merged_mask_out_21.png
data-cells2\annotations\HEK_0009_merged_mask_out_22.png
data-cells2\annotations\HEK_0009_merged_mask_out_23.png
data-cells2\annotations\HEK_0009_merged_mask_out_24.png
data-cells2\annotations\HEK_0009_merged_mask_out_2

data-cells2\annotations\HEK_0011_merged_mask_out_47.png
data-cells2\annotations\HEK_0011_merged_mask_out_48.png
data-cells2\annotations\HEK_0011_merged_mask_out_49.png
data-cells2\annotations\HEK_0011_merged_mask_out_5.png
data-cells2\annotations\HEK_0011_merged_mask_out_50.png
data-cells2\annotations\HEK_0011_merged_mask_out_51.png
data-cells2\annotations\HEK_0011_merged_mask_out_52.png
data-cells2\annotations\HEK_0011_merged_mask_out_53.png
data-cells2\annotations\HEK_0011_merged_mask_out_54.png
data-cells2\annotations\HEK_0011_merged_mask_out_55.png
data-cells2\annotations\HEK_0011_merged_mask_out_56.png
data-cells2\annotations\HEK_0011_merged_mask_out_57.png
data-cells2\annotations\HEK_0011_merged_mask_out_58.png
data-cells2\annotations\HEK_0011_merged_mask_out_59.png
data-cells2\annotations\HEK_0011_merged_mask_out_6.png
data-cells2\annotations\HEK_0011_merged_mask_out_60.png
data-cells2\annotations\HEK_0011_merged_mask_out_61.png
data-cells2\annotations\HEK_0011_merged_mask_out_6

...

data-cells2\annotations\N2a_0613_merged_mask_out_193.png
data-cells2\annotations\N2a_0613_merged_mask_out_194.png
data-cells2\annotations\N2a_0613_merged_mask_out_195.png
data-cells2\annotations\N2a_0613_merged_mask_out_196.png
data-cells2\annotations\N2a_0613_merged_mask_out_197.png
data-cells2\annotations\N2a_0613_merged_mask_out_198.png
data-cells2\annotations\N2a_0613_merged_mask_out_199.png
data-cells2\annotations\N2a_0613_merged_mask_out_2.png
data-cells2\annotations\N2a_0613_merged_mask_out_20.png
data-cells2\annotations\N2a_0613_merged_mask_out_200.png
data-cells2\annotations\N2a_0613_merged_mask_out_201.png
data-cells2\annotations\N2a_0613_merged_mask_out_202.png
data-cells2\annotations\N2a_0613_merged_mask_out_203.png
data-cells2\annotations\N2a_0613_merged_mask_out_204.png
data-cells2\annotations\N2a_0613_merged_mask_out_205.png
data-cells2\annotations\N2a_0613_merged_mask_out_206.png
data-cells2\annotations\N2a_0613_merged_mask_out_207.png
data-cells2\annotations\N2a_0613_m

data-cells2\annotations\N2a_0614_merged_mask_out_102.png
data-cells2\annotations\N2a_0614_merged_mask_out_103.png
data-cells2\annotations\N2a_0614_merged_mask_out_104.png
data-cells2\annotations\N2a_0614_merged_mask_out_105.png
data-cells2\annotations\N2a_0614_merged_mask_out_106.png
data-cells2\annotations\N2a_0614_merged_mask_out_107.png
data-cells2\annotations\N2a_0614_merged_mask_out_108.png
data-cells2\annotations\N2a_0614_merged_mask_out_109.png
data-cells2\annotations\N2a_0614_merged_mask_out_11.png
data-cells2\annotations\N2a_0614_merged_mask_out_110.png
data-cells2\annotations\N2a_0614_merged_mask_out_111.png
data-cells2\annotations\N2a_0614_merged_mask_out_112.png
data-cells2\annotations\N2a_0614_merged_mask_out_113.png
data-cells2\annotations\N2a_0614_merged_mask_out_114.png
data-cells2\annotations\N2a_0614_merged_mask_out_12.png
data-cells2\annotations\N2a_0614_merged_mask_out_13.png
data-cells2\annotations\N2a_0614_merged_mask_out_14.png
data-cells2\annotations\N2a_0614_me

data-cells2\annotations\N2a_0616_merged_mask_out_2.png
data-cells2\annotations\N2a_0616_merged_mask_out_20.png
data-cells2\annotations\N2a_0616_merged_mask_out_21.png
data-cells2\annotations\N2a_0616_merged_mask_out_22.png
data-cells2\annotations\N2a_0616_merged_mask_out_23.png
data-cells2\annotations\N2a_0616_merged_mask_out_24.png
data-cells2\annotations\N2a_0616_merged_mask_out_25.png
data-cells2\annotations\N2a_0616_merged_mask_out_26.png
data-cells2\annotations\N2a_0616_merged_mask_out_27.png
data-cells2\annotations\N2a_0616_merged_mask_out_28.png
data-cells2\annotations\N2a_0616_merged_mask_out_29.png
data-cells2\annotations\N2a_0616_merged_mask_out_3.png
data-cells2\annotations\N2a_0616_merged_mask_out_30.png
data-cells2\annotations\N2a_0616_merged_mask_out_31.png
data-cells2\annotations\N2a_0616_merged_mask_out_32.png
data-cells2\annotations\N2a_0616_merged_mask_out_33.png
data-cells2\annotations\N2a_0616_merged_mask_out_34.png
data-cells2\annotations\N2a_0616_merged_mask_out_3

data-cells2\annotations\N2a_0619_merged_mask_out_62.png
data-cells2\annotations\N2a_0619_merged_mask_out_63.png
data-cells2\annotations\N2a_0619_merged_mask_out_64.png
data-cells2\annotations\N2a_0619_merged_mask_out_7.png
data-cells2\annotations\N2a_0619_merged_mask_out_8.png
data-cells2\annotations\N2a_0619_merged_mask_out_9.png
data-cells2\annotations\N2a_0620_merged_mask_out_1.png
data-cells2\annotations\N2a_0620_merged_mask_out_10.png
data-cells2\annotations\N2a_0620_merged_mask_out_11.png
data-cells2\annotations\N2a_0620_merged_mask_out_12.png
data-cells2\annotations\N2a_0620_merged_mask_out_13.png
data-cells2\annotations\N2a_0620_merged_mask_out_14.png
data-cells2\annotations\N2a_0620_merged_mask_out_15.png
data-cells2\annotations\N2a_0620_merged_mask_out_16.png
data-cells2\annotations\N2a_0620_merged_mask_out_17.png
data-cells2\annotations\N2a_0620_merged_mask_out_18.png
data-cells2\annotations\N2a_0620_merged_mask_out_19.png
data-cells2\annotations\N2a_0620_merged_mask_out_2.p

data-cells2\annotations\N2a_0625_merged_mask_out_34.png
data-cells2\annotations\N2a_0625_merged_mask_out_35.png
data-cells2\annotations\N2a_0625_merged_mask_out_36.png
data-cells2\annotations\N2a_0625_merged_mask_out_37.png
data-cells2\annotations\N2a_0625_merged_mask_out_38.png
data-cells2\annotations\N2a_0625_merged_mask_out_39.png
data-cells2\annotations\N2a_0625_merged_mask_out_4.png
data-cells2\annotations\N2a_0625_merged_mask_out_40.png
data-cells2\annotations\N2a_0625_merged_mask_out_5.png
data-cells2\annotations\N2a_0625_merged_mask_out_6.png
data-cells2\annotations\N2a_0625_merged_mask_out_7.png
data-cells2\annotations\N2a_0625_merged_mask_out_8.png
data-cells2\annotations\N2a_0625_merged_mask_out_9.png
data-cells2\annotations\N2a_0626_merged_mask_out_1.png
data-cells2\annotations\N2a_0626_merged_mask_out_10.png
data-cells2\annotations\N2a_0626_merged_mask_out_11.png
data-cells2\annotations\N2a_0626_merged_mask_out_12.png
data-cells2\annotations\N2a_0626_merged_mask_out_13.png